<a href="https://colab.research.google.com/github/Ruqyai/MENADD-DL/blob/main/RNN/Music_Generator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Music Generator 
Plan was simple:
1. Read midi file, convert it to matrix of features. Look at an example https://onlinesequencer.net/1334388  
2. Create simple model with Keras and LSTM to learn the pattern
3. Use subsample of initial midi file as a input for model to generate pure art
4. Save prediction from model to midi file


In [ ]:
#Mido is a library for working with MIDI messages and ports
!pip install mido &> /dev/null 

In [ ]:
import mido
from mido import MidiFile, MidiTrack, Message #Please Read https://mido.readthedocs.io/en/latest/midi_files.html 
from tensorflow.keras.layers import LSTM, Dense, Activation, Dropout, Flatten
from tensorflow.keras.preprocessing import sequence
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
from sklearn.preprocessing import MinMaxScaler
import numpy as np
from IPython.display import Audio

##### Read midi file

In [ ]:
!wget https://github.com/Ruqyai/MENADD-DL/raw/main/Data/Piano.mid &> /dev/null 

In [ ]:
Audio('Piano.mid')

To understand MIDI structure https://ask.video/embed/midi101/16-16-note-on-and-note-off-message-structure-note-off-variations

In [ ]:
mid = MidiFile('Piano.mid') 
mid

MidiFile(type=1, ticks_per_beat=256, tracks=[
  MidiTrack([
    MetaMessage('set_tempo', tempo=500000, time=0),
    MetaMessage('track_name', name='<Title>', time=0),
    MetaMessage('copyright', text='@<copyright>', time=0),
    MetaMessage('end_of_track', time=0)]),
  MidiTrack([
    MetaMessage('track_name', name='Piano (Left Hand)', time=0),
    Message('control_change', channel=0, control=7, value=127, time=0),
    Message('control_change', channel=0, control=10, value=64, time=0),
    Message('control_change', channel=0, control=0, value=0, time=0),
    Message('control_change', channel=0, control=32, value=0, time=0),
    Message('program_change', channel=0, program=0, time=0),
    Message('control_change', channel=0, control=93, value=0, time=0),
    MetaMessage('time_signature', numerator=4, denominator=4, clocks_per_click=24, notated_32nd_notes_per_beat=8, time=0),
    MetaMessage('key_signature', key='Eb', time=0),
    Message('control_change', channel=0, control=93, value=0

##### Extract notes sequence

In [ ]:
notes = []
for msg in mid:
    if not msg.is_meta and msg.channel == 0 and msg.type == 'note_on':
        data = msg.bytes()
        notes.append(data[1])

In [ ]:
#notes

#### Apply min-max scalling

In [ ]:
scaler = MinMaxScaler(feature_range=(0,1))
scaler.fit(np.array(notes).reshape(-1,1))
notes = list(scaler.transform(np.array(notes).reshape(-1,1)))

In [ ]:
#notes

#### Prepare features for training and data subsample for prediction

In [ ]:
# LSTM layers requires that data must have a certain shape
# create list of lists fist
notes = [list(note) for note in notes]
# subsample data for training and prediction
X = []
y = []
# number of notes in a batch
n_prev = 30
for i in range(len(notes)-n_prev):
    X.append(notes[i:i+n_prev])
    y.append(notes[i+n_prev])
# save a seed to do prediction later
X_test = X[-300:]
X = X[:-300]
y = y[:-300]

In [ ]:
#notes

#### Made sequential model with several layers, use LSTM as it time dependent data



In [ ]:
model = Sequential()
model.add(LSTM(256, input_shape=(n_prev, 1), return_sequences=True))
model.add(Dropout(0.6))
model.add(LSTM(128, input_shape=(n_prev, 1), return_sequences=True))
model.add(Dropout(0.6))
model.add(LSTM(64, input_shape=(n_prev, 1), return_sequences=False))
model.add(Dropout(0.6))
model.add(Dense(1))
model.add(Activation('linear'))

model.compile(loss='mse', optimizer=Adam(learning_rate=0.001))


#### Train your model.


In [ ]:
model.fit(np.array(X), np.array(y), batch_size=32, epochs=3, verbose=1)

Epoch 1/3
400/400 [==============================] - 65s 151ms/step - loss: 0.0519
Epoch 2/3
400/400 [==============================] - 61s 153ms/step - loss: 0.0470
Epoch 3/3
400/400 [==============================] - 61s 152ms/step - loss: 0.0456


#### Make a prediction

In [ ]:
prediction = model.predict(np.array(X_test))
prediction = np.squeeze(prediction)
prediction = np.squeeze(scaler.inverse_transform(prediction.reshape(-1,1)))
prediction = [int(i) for i in prediction]

In [ ]:
#prediction

#### Save your result to new midi file

In [ ]:
mid = MidiFile()
track = MidiTrack()
t = 0
for note in prediction:
    # 147 means note_on
    # 67 is velosity
    note = np.asarray([147, note, 67])
    bytes = note.astype(int)
    #print(bytes)
    msg = Message.from_bytes(bytes[0:3])
    t += 1
    msg.time = t
    track.append(msg)
    #print(msg)
mid.tracks.append(track)
mid.save('New_Music.mid')

In [ ]:
Audio("New_Music.mid")